# Part 3

In [1]:
import pandas as pd
from fuzzywuzzy import fuzz, process
import numpy as np

C:\Users\602770\AppData\Local\Continuum\anaconda3\lib\site-packages\fuzzywuzzy\fuzz.py:11: UserWarning: Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning
  warnings.warn('Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning')


In [2]:
pd.set_option('max_rows', None)
pd.set_option('max_columns', None)

In [3]:
df_potholes = pd.read_csv('Processed Data/Potholes_Aug_to_Oct_19.csv')

In [4]:
df_base = pd.read_csv('Processed Data/df_base.csv')

In [5]:
df_base.head()

streetsegid   street_address  directionality  segmenttype  fromnodeid  \
0     SEGID-1     BANGOR ST SE             2.0          2.0     22041.0   
1     SEGID-2  SOUTHERN AVE SE             2.0          2.0     14495.0   
2     SEGID-3  100 F STREET NE             0.0          2.0     14497.0   
3     SEGID-3  100 F STREET NE             0.0          2.0     14497.0   
4     SEGID-4          O ST NW             2.0          2.0     14499.0   

   tonodeid  fromaddresslefttheo  toaddresslefttheo  fromaddressrighttheo  \
0   21776.0               1430.0             1470.0                1429.0   
1   14496.0               1382.0             1398.0                1383.0   
2   14498.0                100.0              198.0                 101.0   
3   14498.0                100.0              198.0                 101.0   
4   14500.0                330.0              402.0                 401.0   

   toaddressrighttheo  beginmeasure  endmeasure    shapelen  latitude_bv  \
0              1469.0           0.0  180.261072  180.261040     0.000000   
1              1399.0           0.0  195.020180  195.020224     0.000000   
2               199.0           0.0  109.595234  109.595277    38.897347   
3               199.0           0.0  109.595234  109.595277    38.897356   
4               403.0           0.0   23.021826   23.021827     0.000000   

   longitude_bv         requesttype               requestdate  \
0      0.000000                 NaN                       NaN   
1      0.000000                 NaN                       NaN   
2    -77.003755  Other Biking Issue  2015-07-31T14:16:08.000Z   
3    -77.004070  Other Biking Issue  2015-11-12T17:33:05.000Z   
4      0.000000                 NaN                       NaN   

                                            comments usertype  latitude_bc  \
0                                                NaN      NaN     0.000000   
1                                                NaN      NaN     0.000000   
2  Due to the left-straight-right turn arrows her...    Biker    38.897341   
3                                     Giant potholes    Biker    38.897341   
4                                                NaN      NaN     0.000000   

   longitude_bc  fatal_bicyclist  majorinjuries_bicyclist  \
0      0.000000              0.0                      0.0   
1      0.000000              0.0                      0.0   
2    -77.004179              0.0                      0.0   
3    -77.004179              0.0                      0.0   
4      0.000000              0.0                      0.0   

   minorinjuries_bicyclist  bicyclistsimpaired                reportdate  \
0                      0.0                 0.0                       NaN   
1                      0.0                 0.0                       NaN   
2                      1.0                 0.0  2018-05-31T18:01:43.000Z   
3                      1.0                 0.0  2018-05-31T18:01:43.000Z   
4                      0.0                 0.0                       NaN   

     ward  
0     NaN  
1     NaN  
2  Ward 6  
3  Ward 6  
4     NaN

In [6]:
df_potholes.head()

objectid   latitude  longitude                   adddate  \
0         1  38.822440 -77.018104  2019-08-08T15:59:43.000Z   
1         2  38.935170 -77.057232  2019-08-10T20:21:17.000Z   
2         3  38.867553 -76.946423  2019-08-12T15:20:44.000Z   
3         4  38.917934 -77.045490  2019-08-06T16:43:09.000Z   
4         5  38.963308 -77.075336  2019-08-19T08:31:15.000Z   

             resolutiondate                       street_address  zipcode  \
0  2019-08-09T07:48:15.000Z              4555 OVERLOOK AVENUE SW    20375   
1  2019-08-12T18:55:04.000Z                2738 ORDWAY STREET NW    20008   
2  2019-08-13T16:25:11.000Z             1600 FORT DAVIS PLACE SE    20020   
3  2019-08-08T16:43:22.000Z  20TH STREET NW AND COLUMBIA ROAD NW    20009   
4  2019-08-22T09:15:12.000Z            3815 LIVINGSTON STREET NW    20015   

   ward  
0   8.0  
1   3.0  
2   7.0  
3   1.0  
4   3.0

In [7]:
list(df_potholes['street_address'].sort_values().unique())

['1 - 38 BLOCK OF FLORIDA AVENUE NE',
 '1 THOMAS CIRCLE NW',
 '10 ADAMS STREET NW',
 '100 - 199 BLOCK OF 4TH STREET SW',
 '100 INDIANA AVENUE NW',
 '1000 - 1199 BLOCK OF INDEPENDENCE AVENUE SW',
 '1000 THOMAS JEFFERSON STREET NW',
 '1001 K STREET NW',
 '1005 DOUGLAS STREET NE',
 '1007 ALABAMA AVENUE SE',
 '101 H STREET NE',
 '1015 HALF STREET SE',
 '1016 5TH STREET NE',
 '1023 E STREET SE',
 '1025 MICHIGAN AVENUE NE',
 '104 47TH STREET NE',
 '104 55TH STREET NE',
 '1063 WISCONSIN AVENUE NW',
 '1065 48TH PLACE NE',
 '109 19TH STREET SE',
 '1090 VERMONT AVENUE NW',
 '10TH PLACE SE AND ALABAMA AVENUE SE',
 '10TH STREET NE AND CONSTITUTION AVENUE NE',
 '10TH STREET NW AND CONSTITUTION AVENUE NW',
 '10TH STREET NW AND K STREET NW',
 '11 RIGGS ROAD NE',
 '1100 - 1199 BLOCK OF ALABAMA AVENUE SE',
 '1100 ALABAMA AVENUE SE',
 '1100 K STREET SE',
 '1100 NORTH CAPITOL STREET NW',
 '1101 1ST STREET NE',
 '1101 CONNECTICUT AVENUE NW',
 '1106 BARNABY TERRACE SE',
 '1108 21ST PLACE NE',
 '1108 QUEEN 

In [8]:
# Then once all of that has been taken care of, we need to merge with potholes - issue is there is no segid
    #So, use fuzzymatching/levensthein distance to try to match on street_address
    #Accept cases where match is at least 80%?

# get a list of all unique df_base addresses - much longer 
segid_addresses = list(df_base['street_address'].sort_values().unique())

# get a list of all unique df_potholes addresses
potholes_addresses = list(df_potholes['street_address'].sort_values().unique())

In [9]:
segid_match = []

for i in segid_addresses:
    
    segid_match.append([i])

In [10]:
len(list(df_base['street_address'].sort_values().unique()))

3975

In [11]:
# Takes some time to run - around 10 minutes

segid_match = []

# get a list of all unique df_base addresses - much longer 
segid_addresses = list(df_base['street_address'].sort_values().unique())

# get a list of all unique df_potholes addresses
potholes_addresses = list(df_potholes['street_address'].sort_values().unique())

for i in segid_addresses:

    segid_match.append([i])


# for each unique df_base address, get levensthein distance with all the potholes addresses
# If score is above 60, append it to segid_match using the correct index of the segid_addresses and store as a vector 

    
for i in segid_addresses:

    for j in potholes_addresses:

        if fuzz.token_set_ratio(i,j) > 95:

            segid_match[segid_addresses.index(i)].append(fuzz.token_set_ratio(i,j))

        else:
            segid_match[segid_addresses.index(i)].append(0)


#From there, determine a decent threshold - 95 - needs to be pretty high to be even remotely close geographically 

# Create a dataframe with df_base address & best-matching potholes address - assuming they are on same street/segment
# Merge this dataframe with df_bases
# Then merge new df_bases with df_potholes on the best-matching address as the key
# Now we have pothole data based off of segid even though potholes are not recorded by segid


In [12]:
#Flipping axes by Transposing 
df_segid = pd.DataFrame(segid_match).T

#Making the first row the header
headers = df_segid.iloc[0] #grab the first row for the header
df_segid = df_segid[1:]

#Need to make sure the values are int64 data type

cols = df_segid.columns
df_segid[cols] = df_segid[cols].apply(pd.to_numeric, errors='coerce')
df_segid.columns = headers

In [13]:
df_segid.to_csv('Processed Data/fuzzy_frame.csv', index=False)

In [14]:
df_segid = pd.read_csv('Processed Data/fuzzy_frame.csv')

In [15]:
df_segid.head()

0 FRANCIS SCOTT KEY BRG NW  1 11TH ST NE  1 1ST STREET NE  1 GRANT CIR NW  \
0                           0             0                0               0   
1                           0             0                0               0   
2                           0             0                0               0   
3                           0             0                0               0   
4                           0             0                0               0   

   1 MICHIGAN AVENUE NW  1 RHODE ISLAND AVENUE NE  10 3RD STREET SE  \
0                     0                         0                 0   
1                     0                         0                 0   
2                     0                         0                 0   
3                     0                         0                 0   
4                     0                         0                 0   

   10 D ST NE  10 I STREET SW  10 M STREET NW  10 P STREET NE  \
0           0               0               0               0   
1           0               0               0               0   
2           0               0               0               0   
3           0               0               0               0   
4           0               0               0               0   

   10 THOMAS CIRCLE NW  100 15TH ST. NW.  100 BLOCK RHODE ISLAND AVE NE  \
0                    0                 0                              0   
1                   97                 0                              0   
2                    0                 0                              0   
3                    0                 0                              0   
4                    0                 0                              0   

   100 EAST CAPITOL STREET NE  100 F STREET NE  100 FIRST ST NW  \
0                           0                0                0   
1                           0                0                0   
2                           0                0                0   
3                           0                0                0   
4                           0                0                0   

   100 GALLATIN STREET NE  100 INDEPENDENCE AVE SW  100 IRVING STREET NW  \
0                       0                        0                     0   
1                       0                        0                     0   
2                       0                        0                     0   
3                       0                        0                     0   
4                       0                        0                     0   

   100 K STREEE NW  100 K STREET NE  100 LO  100 MASSACHUSETTS AVE NE  \
0                0                0       0                         0   
1                0                0       0                         0   
2                0                0       0                         0   
3                0                0       0                         0   
4                0                0       0                         0   

   100 MICHIGAN AVENUE NE  100 NEW YORK AVENUE NE  \
0                       0                       0   
1                       0                       0   
2                       0                       0   
3                       0                       0   
4                       0                       0   

   100 ROCK CREEK & POTOMAC PARKWAY NW  1000 15TH ST NW  1000 17TH ST NW  \
0                                    0                0                0   
1                                    0                0                0   
2                                    0                0                0   
3                                    0                0                0   
4                                    0                0                0   

   1000 1ST STREET NW  1000 4TH STREET SW  1000 6TH STREET SW  \
0                   0                   0                   0   
1                   0                   0       

In [3]:
# Verifying the closeness of match based off of leve. distance
segid_addresses[24]
potholes_addresses[461]
fuzz.token_set_ratio('10 M STREET NW' , potholes_addresses[461])

NameError: name 'segid_addresses' is not defined

In [4]:
fuzz.token_set_ratio("ALPENA COUNTY REGIONAL AIRPORT", "ALPENA CO REG APT")

72

In [17]:
#Best score for each segid address
df_segid.max()

0 FRANCIS SCOTT KEY BRG NW                                    0
1 11TH ST NE                                                  0
1 1ST STREET NE                                               0
1 GRANT CIR NW                                                0
1 MICHIGAN AVENUE NW                                          0
1 RHODE ISLAND AVENUE NE                                     98
10 3RD STREET SE                                              0
10 D ST NE                                                    0
10 I STREET SW                                                0
10 M STREET NW                                               97
10 P STREET NE                                                0
10 THOMAS CIRCLE NW                                          97
100 15TH ST. NW.                                              0
100 BLOCK RHODE ISLAND AVE NE                                 0
100 EAST CAPITOL STREET NE                                   98
100 F STREET NE                         

In [18]:
#Gives us the index of the fuzzymatch with the highest score
best_indexes = df_segid.idxmax()
best_indexes

0 FRANCIS SCOTT KEY BRG NW                                    0
1 11TH ST NE                                                  0
1 1ST STREET NE                                               0
1 GRANT CIR NW                                                0
1 MICHIGAN AVENUE NW                                          0
1 RHODE ISLAND AVENUE NE                                     84
10 3RD STREET SE                                              0
10 D ST NE                                                    0
10 I STREET SW                                                0
10 M STREET NW                                              520
10 P STREET NE                                                0
10 THOMAS CIRCLE NW                                           1
100 15TH ST. NW.                                              0
100 BLOCK RHODE ISLAND AVE NE                                 0
100 EAST CAPITOL STREET NE                                   90
100 F STREET NE                         

In [19]:
matches = pd.DataFrame(best_indexes)
matches.reset_index(inplace=True)
matches.columns = ['street_address','Pothole Address Index']

matches

street_address  Pothole Address Index
0                            0 FRANCIS SCOTT KEY BRG NW                      0
1                                          1 11TH ST NE                      0
2                                       1 1ST STREET NE                      0
3                                        1 GRANT CIR NW                      0
4                                  1 MICHIGAN AVENUE NW                      0
5                              1 RHODE ISLAND AVENUE NE                     84
6                                      10 3RD STREET SE                      0
7                                            10 D ST NE                      0
8                                        10 I STREET SW                      0
9                                        10 M STREET NW                    520
10                                       10 P STREET NE                      0
11                                  10 THOMAS CIRCLE NW                      1
12                                     100 15TH ST. NW.                      0
13                        100 BLOCK RHODE ISLAND AVE NE                      0
14                           100 EAST CAPITOL STREET NE                     90
15                                      100 F STREET NE                      0
16                                      100 FIRST ST NW                      0
17                               100 GALLATIN STREET NE                      0
18                              100 INDEPENDENCE AVE SW                      0
19                                 100 IRVING STREET NW                      0
20                                      100 K STREEE NW                      0
21                                      100 K STREET NE                      0
22                                               100 LO                      0
23                             100 MASSACHUSETTS AVE NE                      0
24                               100 MICHIGAN AVENUE NE                      0
25                               100 NEW YORK AVENUE NE                      0
26                  100 ROCK CREEK & POTOMAC PARKWAY NW                      0
27                                      1000 15TH ST NW                      0
28                                      1000 17TH ST NW                      0
29                                   1000 1ST STREET NW                      0
30                                   1000 4TH STREET SW                      0
31                                   1000 6TH STREET SW                      0
32                                   1000 8TH STREET NE                      0
33                             1000 BLADENSBURG ROAD NE                    206
34                           1000 CONNECTICUT AVENUE NW                      0
35                          1000 EAST CAPITOL STREET NE                     90
36                                     1000 F STREET NW                      0
37                                 1000 MAINE AVENUE SW                      0
38                              1000 PENNSYLANIA AVE NW                      0
39                             1000 PENNSYLVANIA AVE NW                      0
40                                     1000 R STREET NW                      0
41                          1000 RHODE ISLAND AVENUE NW                      0
42                                     1000 U STREET NW                      0
43                             1000 WISCONSIN AVENUE NW                      0
44                                  1001 14TH STREET NW                      0
45                                   1001 4TH STREET NW                      0
46                                   1001 6TH STREET NW                      0
47                                1001 IRVING STREET NW                      0
48                         1001 NEW HAMPSHIRE AVENUE NW                      0
49                              1001 NEW YORK AVENUE NW                      0
50          

In [20]:
matches = matches[matches['Pothole Address Index'] != 0 ]
matches

street_address  Pothole Address Index
5                        1 RHODE ISLAND AVENUE NE                     84
9                                  10 M STREET NW                    520
11                            10 THOMAS CIRCLE NW                      1
14                     100 EAST CAPITOL STREET NE                     90
33                       1000 BLADENSBURG ROAD NE                    206
35                    1000 EAST CAPITOL STREET NE                     90
62                        1020 MICHIGAN AVENUE NE                     14
94                     1100 CONNECTICUT AVENUE NW                     31
95                    1100 EAST CAPITOL STREET NE                     90
120                  1101 WEST VIRGINIA AVENUE NE                    115
170                                11TH STREET NW                    205
177                                11TH STREET SE                    256
183                      1200 BLADENSBURG ROAD NE                    206
186                   1200 EAST CAPITOL STREET NE                     90
196                  1200 NORTH CAPITOL STREET NW                     29
204                    1201 CONNECTICUT AVENUE NW                     31
205                   1201 CONSTITUTION AVENUE NW                    113
208                       1201 NEW YORK AVENUE NW                     74
209                  1201 WEST VIRGINIA AVENUE NE                     63
220                  1213 WEST VIRGINIA AVENUE NE                     63
229                       1235 NEW YORK AVENUE NW                     74
230                     1236 MOUNT OLIVET ROAD NE                     69
233                        125 MICHIGAN AVENUE NE                     14
270                   1300 PENNSYLVANIA AVENUE NW                    103
276                   1301 CONSTITUTION AVENUE NW                    113
277                              1301 K STREET NW                     93
278                   1301 PENNSYLVANIA AVENUE NW                    103
280                   1305 RHODE ISLAND AVENUE NE                     84
299                   1350 PENNSYLVANIA AVENUE NW                    103
328                                13TH STREET NW                     68
355                  1400 NORTH CAPITOL STREET NW                     29
360                   1401 CONSTITUTION AVENUE NW                    113
366                  1403 WEST VIRGINIA AVENUE NE                    114
468                  1500 NORTH CAPITOL STREET NW                     29
469                   1500 PENNSYLVANIA AVENUE NW                    103
482                    1512 CONNECTICUT AVENUE NW                    137
520                                15TH STREET NW                    146
528                               15TH STREET, NW                    146
542                  1600 NORTH CAPITOL STREET NW                     29
545                    1601 CONNECTICUT AVENUE NW                     31
566                    163 RHODE ISLAND AVENUE NE                     84
568                    1636 CONNECTICUT AVENUE NW                    155
573                    1666 CONNECTICUT AVENUE NW                    155
589                                16TH STREET NW                    158
590           16TH STREET NW & ARKANSAS AVENUE NW                    159
615                     1700 NEW JERSEY AVENUE NW                    173
641                   1730 PENNSYLVANIA AVENUE NW                    103
686                         1800 COLUMBIA ROAD NW                    178
694                       1801 NEW YORK AVENUE NE                    188
744                                18TH STREET NW                    190
769                            1909 9TH STREET NW                    193
771                   1913 RHODE ISLAND AVENUE NE                     84
819                                 1ST STREET NE                     30
827              1ST STREET NW & IRVING STREET NW                    202
834                 

In [21]:
len(matches)

143

In [22]:
# Merge this dataframe with df_bases
# Then merge new df_bases with df_potholes on the best-matching address as the key
# Now we have pothole data based off of segid even though potholes are not recorded by segid

In [23]:
valores = np.array(matches['Pothole Address Index'])

select_potholes_addresses = []

for i in valores:

    select_potholes_addresses.append(potholes_addresses[i])

In [24]:
select_potholes_addresses

['13 RHODE ISLAND AVENUE NE',
 '610 M STREET NW',
 '1 THOMAS CIRCLE NW',
 '1300 EAST CAPITOL STREET NE',
 '2000 BLADENSBURG ROAD NE',
 '1300 EAST CAPITOL STREET NE',
 '1025 MICHIGAN AVENUE NE',
 '1101 CONNECTICUT AVENUE NW',
 '1300 EAST CAPITOL STREET NE',
 '1411 WEST VIRGINIA AVENUE NE',
 '2000 - 2099 BLOCK OF 11TH STREET NW',
 '251 11TH STREET SE',
 '2000 BLADENSBURG ROAD NE',
 '1300 EAST CAPITOL STREET NE',
 '1100 NORTH CAPITOL STREET NW',
 '1101 CONNECTICUT AVENUE NW',
 '1401 CONSTITUTION AVENUE NW',
 '1250 NEW YORK AVENUE NW',
 '1217 WEST VIRGINIA AVENUE NE',
 '1217 WEST VIRGINIA AVENUE NE',
 '1250 NEW YORK AVENUE NW',
 '1237 MOUNT OLIVET ROAD NE',
 '1025 MICHIGAN AVENUE NE',
 '1350 PENNSYLVANIA AVENUE NW',
 '1401 CONSTITUTION AVENUE NW',
 '1301 K STREET NW',
 '1350 PENNSYLVANIA AVENUE NW',
 '13 RHODE ISLAND AVENUE NE',
 '1350 PENNSYLVANIA AVENUE NW',
 '1230 13TH STREET NW',
 '1100 NORTH CAPITOL STREET NW',
 '1401 CONSTITUTION AVENUE NW',
 '1405 WEST VIRGINIA AVENUE NE',
 '1100 NO

In [25]:
matches['potholes_addresses'] = select_potholes_addresses

C:\Users\602770\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


In [26]:
matches

street_address  Pothole Address Index  \
5                        1 RHODE ISLAND AVENUE NE                     84   
9                                  10 M STREET NW                    520   
11                            10 THOMAS CIRCLE NW                      1   
14                     100 EAST CAPITOL STREET NE                     90   
33                       1000 BLADENSBURG ROAD NE                    206   
35                    1000 EAST CAPITOL STREET NE                     90   
62                        1020 MICHIGAN AVENUE NE                     14   
94                     1100 CONNECTICUT AVENUE NW                     31   
95                    1100 EAST CAPITOL STREET NE                     90   
120                  1101 WEST VIRGINIA AVENUE NE                    115   
170                                11TH STREET NW                    205   
177                                11TH STREET SE                    256   
183                      1200 BLADENSBURG ROAD NE                    206   
186                   1200 EAST CAPITOL STREET NE                     90   
196                  1200 NORTH CAPITOL STREET NW                     29   
204                    1201 CONNECTICUT AVENUE NW                     31   
205                   1201 CONSTITUTION AVENUE NW                    113   
208                       1201 NEW YORK AVENUE NW                     74   
209                  1201 WEST VIRGINIA AVENUE NE                     63   
220                  1213 WEST VIRGINIA AVENUE NE                     63   
229                       1235 NEW YORK AVENUE NW                     74   
230                     1236 MOUNT OLIVET ROAD NE                     69   
233                        125 MICHIGAN AVENUE NE                     14   
270                   1300 PENNSYLVANIA AVENUE NW                    103   
276                   1301 CONSTITUTION AVENUE NW                    113   
277                              1301 K STREET NW                     93   
278                   1301 PENNSYLVANIA AVENUE NW                    103   
280                   1305 RHODE ISLAND AVENUE NE                     84   
299                   1350 PENNSYLVANIA AVENUE NW                    103   
328                                13TH STREET NW                     68   
355                  1400 NORTH CAPITOL STREET NW                     29   
360                   1401 CONSTITUTION AVENUE NW                    113   
366                  1403 WEST VIRGINIA AVENUE NE                    114   
468                  1500 NORTH CAPITOL STREET NW                     29   
469                   1500 PENNSYLVANIA AVENUE NW                    103   
482                    1512 CONNECTICUT AVENUE NW                    137   
520                                15TH STREET NW                    146   
528                               15TH STREET, NW                    146   
542                  1600 NORTH CAPITOL STREET NW                     29   
545                    1601 CONNECTICUT AVENUE NW                     31   
566                    163 RHODE ISLAND AVENUE NE                     84   
568                    1636 CONNECTICUT AVENUE NW                    155   
573                    1666 CONNECTICUT AVENUE NW                    155   
589                                16TH STREET NW                    158   
590           16TH STREET NW & ARKANSAS AVENUE NW                    159   
615                     1700 NEW JERSEY AVENUE NW                    173   
641                   1730 PENNSYLVANIA AVENUE NW                    103   
686                         1800 COLUMBIA ROAD NW                    178   
694                       1801 NEW YORK AVENUE NE                    188   
744                                18TH STREET NW                    190   
769                            1909 9TH STREET NW                    193   
771                   1913 RHODE ISLAND AVENUE NE                     84   
819    

In [27]:
a=len(df_potholes)
b=len(matches)

print('Total Potholes:', a, '\nMatches', b, '\nRatio', b/a) 

Total Potholes: 916 
Matches 143 
Ratio 0.15611353711790393


In [28]:
df_potholes.head()

objectid   latitude  longitude                   adddate  \
0         1  38.822440 -77.018104  2019-08-08T15:59:43.000Z   
1         2  38.935170 -77.057232  2019-08-10T20:21:17.000Z   
2         3  38.867553 -76.946423  2019-08-12T15:20:44.000Z   
3         4  38.917934 -77.045490  2019-08-06T16:43:09.000Z   
4         5  38.963308 -77.075336  2019-08-19T08:31:15.000Z   

             resolutiondate                       street_address  zipcode  \
0  2019-08-09T07:48:15.000Z              4555 OVERLOOK AVENUE SW    20375   
1  2019-08-12T18:55:04.000Z                2738 ORDWAY STREET NW    20008   
2  2019-08-13T16:25:11.000Z             1600 FORT DAVIS PLACE SE    20020   
3  2019-08-08T16:43:22.000Z  20TH STREET NW AND COLUMBIA ROAD NW    20009   
4  2019-08-22T09:15:12.000Z            3815 LIVINGSTON STREET NW    20015   

   ward  
0   8.0  
1   3.0  
2   7.0  
3   1.0  
4   3.0

In [29]:
df_potholes.rename(columns={'street_address':'potholes_addresses', 'latitude':'latitude_p', 'longitude':'longitude_p'}, inplace=True)

In [30]:
df_potholes.head()

objectid  latitude_p  longitude_p                   adddate  \
0         1   38.822440   -77.018104  2019-08-08T15:59:43.000Z   
1         2   38.935170   -77.057232  2019-08-10T20:21:17.000Z   
2         3   38.867553   -76.946423  2019-08-12T15:20:44.000Z   
3         4   38.917934   -77.045490  2019-08-06T16:43:09.000Z   
4         5   38.963308   -77.075336  2019-08-19T08:31:15.000Z   

             resolutiondate                   potholes_addresses  zipcode  \
0  2019-08-09T07:48:15.000Z              4555 OVERLOOK AVENUE SW    20375   
1  2019-08-12T18:55:04.000Z                2738 ORDWAY STREET NW    20008   
2  2019-08-13T16:25:11.000Z             1600 FORT DAVIS PLACE SE    20020   
3  2019-08-08T16:43:22.000Z  20TH STREET NW AND COLUMBIA ROAD NW    20009   
4  2019-08-22T09:15:12.000Z            3815 LIVINGSTON STREET NW    20015   

   ward  
0   8.0  
1   3.0  
2   7.0  
3   1.0  
4   3.0

In [31]:
df_base.head()

streetsegid   street_address  directionality  segmenttype  fromnodeid  \
0     SEGID-1     BANGOR ST SE             2.0          2.0     22041.0   
1     SEGID-2  SOUTHERN AVE SE             2.0          2.0     14495.0   
2     SEGID-3  100 F STREET NE             0.0          2.0     14497.0   
3     SEGID-3  100 F STREET NE             0.0          2.0     14497.0   
4     SEGID-4          O ST NW             2.0          2.0     14499.0   

   tonodeid  fromaddresslefttheo  toaddresslefttheo  fromaddressrighttheo  \
0   21776.0               1430.0             1470.0                1429.0   
1   14496.0               1382.0             1398.0                1383.0   
2   14498.0                100.0              198.0                 101.0   
3   14498.0                100.0              198.0                 101.0   
4   14500.0                330.0              402.0                 401.0   

   toaddressrighttheo  beginmeasure  endmeasure    shapelen  latitude_bv  \
0              1469.0           0.0  180.261072  180.261040     0.000000   
1              1399.0           0.0  195.020180  195.020224     0.000000   
2               199.0           0.0  109.595234  109.595277    38.897347   
3               199.0           0.0  109.595234  109.595277    38.897356   
4               403.0           0.0   23.021826   23.021827     0.000000   

   longitude_bv         requesttype               requestdate  \
0      0.000000                 NaN                       NaN   
1      0.000000                 NaN                       NaN   
2    -77.003755  Other Biking Issue  2015-07-31T14:16:08.000Z   
3    -77.004070  Other Biking Issue  2015-11-12T17:33:05.000Z   
4      0.000000                 NaN                       NaN   

                                            comments usertype  latitude_bc  \
0                                                NaN      NaN     0.000000   
1                                                NaN      NaN     0.000000   
2  Due to the left-straight-right turn arrows her...    Biker    38.897341   
3                                     Giant potholes    Biker    38.897341   
4                                                NaN      NaN     0.000000   

   longitude_bc  fatal_bicyclist  majorinjuries_bicyclist  \
0      0.000000              0.0                      0.0   
1      0.000000              0.0                      0.0   
2    -77.004179              0.0                      0.0   
3    -77.004179              0.0                      0.0   
4      0.000000              0.0                      0.0   

   minorinjuries_bicyclist  bicyclistsimpaired                reportdate  \
0                      0.0                 0.0                       NaN   
1                      0.0                 0.0                       NaN   
2                      1.0                 0.0  2018-05-31T18:01:43.000Z   
3                      1.0                 0.0  2018-05-31T18:01:43.000Z   
4                      0.0                 0.0                       NaN   

     ward  
0     NaN  
1     NaN  
2  Ward 6  
3  Ward 6  
4     NaN

In [32]:
#Merging df_base with the matches key so we can merge the potholes data
df_with_potholes = pd.merge(df_base, matches, how='left', on='street_address')

In [33]:
#Making sure we convert nan float to 'NaN' string
type(df_with_potholes['potholes_addresses'][0])

float

In [34]:
df_with_potholes['potholes_addresses'] = df_with_potholes['potholes_addresses'].fillna('NaN')
df_with_potholes['potholes_addresses'].head()

0    NaN
1    NaN
2    NaN
3    NaN
4    NaN
Name: potholes_addresses, dtype: object

In [35]:
df_with_potholes.dtypes

streetsegid                 object
street_address              object
directionality             float64
segmenttype                float64
fromnodeid                 float64
tonodeid                   float64
fromaddresslefttheo        float64
toaddresslefttheo          float64
fromaddressrighttheo       float64
toaddressrighttheo         float64
beginmeasure               float64
endmeasure                 float64
shapelen                   float64
latitude_bv                float64
longitude_bv               float64
requesttype                 object
requestdate                 object
comments                    object
usertype                    object
latitude_bc                float64
longitude_bc               float64
fatal_bicyclist            float64
majorinjuries_bicyclist    float64
minorinjuries_bicyclist    float64
bicyclistsimpaired         float64
reportdate                  object
ward                        object
Pothole Address Index      float64
potholes_addresses  

In [36]:
df_with_potholes.drop(axis=1, columns=['Pothole Address Index'], inplace=True)
df_with_potholes.head()

streetsegid   street_address  directionality  segmenttype  fromnodeid  \
0     SEGID-1     BANGOR ST SE             2.0          2.0     22041.0   
1     SEGID-2  SOUTHERN AVE SE             2.0          2.0     14495.0   
2     SEGID-3  100 F STREET NE             0.0          2.0     14497.0   
3     SEGID-3  100 F STREET NE             0.0          2.0     14497.0   
4     SEGID-4          O ST NW             2.0          2.0     14499.0   

   tonodeid  fromaddresslefttheo  toaddresslefttheo  fromaddressrighttheo  \
0   21776.0               1430.0             1470.0                1429.0   
1   14496.0               1382.0             1398.0                1383.0   
2   14498.0                100.0              198.0                 101.0   
3   14498.0                100.0              198.0                 101.0   
4   14500.0                330.0              402.0                 401.0   

   toaddressrighttheo  beginmeasure  endmeasure    shapelen  latitude_bv  \
0              1469.0           0.0  180.261072  180.261040     0.000000   
1              1399.0           0.0  195.020180  195.020224     0.000000   
2               199.0           0.0  109.595234  109.595277    38.897347   
3               199.0           0.0  109.595234  109.595277    38.897356   
4               403.0           0.0   23.021826   23.021827     0.000000   

   longitude_bv         requesttype               requestdate  \
0      0.000000                 NaN                       NaN   
1      0.000000                 NaN                       NaN   
2    -77.003755  Other Biking Issue  2015-07-31T14:16:08.000Z   
3    -77.004070  Other Biking Issue  2015-11-12T17:33:05.000Z   
4      0.000000                 NaN                       NaN   

                                            comments usertype  latitude_bc  \
0                                                NaN      NaN     0.000000   
1                                                NaN      NaN     0.000000   
2  Due to the left-straight-right turn arrows her...    Biker    38.897341   
3                                     Giant potholes    Biker    38.897341   
4                                                NaN      NaN     0.000000   

   longitude_bc  fatal_bicyclist  majorinjuries_bicyclist  \
0      0.000000              0.0                      0.0   
1      0.000000              0.0                      0.0   
2    -77.004179              0.0                      0.0   
3    -77.004179              0.0                      0.0   
4      0.000000              0.0                      0.0   

   minorinjuries_bicyclist  bicyclistsimpaired                reportdate  \
0                      0.0                 0.0                       NaN   
1                      0.0                 0.0                       NaN   
2                      1.0                 0.0  2018-05-31T18:01:43.000Z   
3                      1.0                 0.0  2018-05-31T18:01:43.000Z   
4                      0.0                 0.0                       NaN   

     ward potholes_addresses  
0     NaN                NaN  
1     NaN                NaN  
2  Ward 6                NaN  
3  Ward 6                NaN  
4     NaN                NaN

In [37]:
df_final = pd.merge(df_with_potholes, df_potholes, how='left', on=['potholes_addresses'])

In [38]:
df_final.head(300)

streetsegid                            street_address  directionality  \
0       SEGID-1                              BANGOR ST SE             2.0   
1       SEGID-2                           SOUTHERN AVE SE             2.0   
2       SEGID-3                           100 F STREET NE             0.0   
3       SEGID-3                           100 F STREET NE             0.0   
4       SEGID-4                                   O ST NW             2.0   
5       SEGID-5                  FLORIDA AVE NE / P ST NE             2.0   
6       SEGID-6                               GALEN ST SE             2.0   
7       SEGID-7                                18TH ST SE             2.0   
8       SEGID-8                                12TH ST NW             0.0   
9       SEGID-9                                14TH ST NE             2.0   
10     SEGID-10                                 4TH ST SE             0.0   
11     SEGID-11                                   O ST NW             2.0   
12     SEGID-12                                   T ST NW             1.0   
13     SEGID-13                            WHITTIER ST NW             2.0   
14     SEGID-14                            INDIANA AVE NW             2.0   
15     SEGID-14                            INDIANA AVE NW             2.0   
16     SEGID-14                            INDIANA AVE NW             2.0   
17     SEGID-14                            INDIANA AVE NW             2.0   
18     SEGID-15                                19TH ST NW             1.0   
19     SEGID-15                                19TH ST NW             1.0   
20     SEGID-16                           MARYLAND AVE SW             2.0   
21     SEGID-17                                 8TH ST NW             2.0   
22     SEGID-18                             WEBSTER ST NW             0.0   
23     SEGID-19                                   K ST SE             1.0   
24     SEGID-20                           HOLBROOK TER NE             2.0   
25     SEGID-22                         KENILWORTH AVE NE             0.0   
26     SEGID-23                                13TH ST SE             2.0   
27     SEGID-24                          CHESAPEAKE ST NW             2.0   
28     SEGID-25                                30TH ST SE             2.0   
29     SEGID-26                                   H ST NE             2.0   
30     SEGID-27                                   C ST NE             1.0   
31     SEGID-28               239 MASSACHUSETTS AVENUE NE             0.0   
32     SEGID-29                                 4TH ST NE             1.0   
33     SEGID-30                                   P ST NW             2.0   
34     SEGID-32                                10TH ST NW             1.0   
35     SEGID-33                              CORBIN PL NE             1.0   
36     SEGID-34                   1500 TRINIDAD AVENUE NE             0.0   
37     SEGID-35                           MONTELLO AVE NE             1.0   
38     SEGID-36                                   Q ST SE             2.0   
39     SEGID-37                                   K ST SE             0.0   
40     SEGID-38                               ALLEN PL NW             2.0   
41     SEGID-39                                   B ST SE             0.0   
42     SEGID-40                                52ND ST NE             2.0   
43     SEGID-41                       SOUTH DAKOTA AVE NE             2.0   
44     SEGID-42                            CENTRAL AVE NE             2.0   
45     SEGID-43                       SOUTH DAKOTA AVE NE             2.0   
46     SEGID-44                                   H ST NW             1.0   
47     SEGID-45                             HILLYER PL NW             1.0   
48     SEGID-46                                   O ST NE             2.0   
49     SEGID-47                         BLADENSBURG RD NE             2.0   
50     SEGID-48                                17TH ST NW             1.0   


In [39]:
c = len(df_final[df_final['potholes_addresses'] != 'NaN'])
d = len(df_final)

print(c,   d, c/d)

420 16495 0.025462261291300393


In [40]:
df_lights = pd.read_csv('Processed Data/Lights.csv')

In [41]:
df_lights.head()

Longitude   Latitude  numberlights streetname  streetsegmid  ward
0 -77.035705  38.901943             1       K ST           555     2
1 -76.985184  38.869033             1    14TH ST          1661     8
2 -76.979626  38.863385             1       V ST          2883     8
3 -76.971740  38.872472             1   WHITE PL          2561     8
4 -76.974904  38.868505             1    22ND ST          2645     8

In [42]:
df_lights.rename(columns={'streetsegmid':'streetsegid', 'numberlights':'number_lights',
                         'Longitude':'longitude_li', 'Latitude':'latitude_li'}, inplace=True)

In [43]:
df_lights.dtypes

longitude_li     float64
latitude_li      float64
number_lights      int64
streetname        object
streetsegid        int64
ward               int64
dtype: object

In [44]:
df_lights.tail()

longitude_li  latitude_li  number_lights       streetname  streetsegid  \
70743    -76.994674    38.862532              1       SHANNON PL         3576   
70744    -77.089859    38.951600              1          46TH ST         8208   
70745    -77.013588    38.963237              1           2ND ST         7435   
70746    -76.920459    38.886682              1          56TH PL          525   
70747    -76.977384    38.843692              1  MISSISSIPPI AVE        10652   

       ward  
70743     8  
70744     3  
70745     4  
70746     7  
70747     8

In [45]:
df_lights['streetsegid'] = df_lights['streetsegid'].astype(str)
df_lights['streetsegid'] = 'SEGID-' + df_lights['streetsegid']

In [46]:
df_lights.head(200)

longitude_li  latitude_li  number_lights                 streetname  \
0      -77.035705    38.901943              1                       K ST   
1      -76.985184    38.869033              1                    14TH ST   
2      -76.979626    38.863385              1                       V ST   
3      -76.971740    38.872472              1                   WHITE PL   
4      -76.974904    38.868505              1                    22ND ST   
5      -76.966617    38.857364              1                    ERIE ST   
6      -76.986230    38.865118              1                       V ST   
7      -76.969018    38.855865              1                    28TH ST   
8      -77.072352    38.943475              1                    37TH ST   
9      -77.032637    38.911747              1                CORCORAN ST   
10     -77.042866    38.915409              1                       T ST   
11     -77.069920    38.951369              1              CUMBERLAND ST   
12     -77.068638    38.952151              1               DAVENPORT ST   
13     -77.110230    38.934081              1             MACARTHUR BLVD   
14     -77.109887    38.933616              1             MACARTHUR BLVD   
15     -77.107747    38.931631              1                  MACOMB ST   
16     -77.106858    38.930600              1             MACARTHUR BLVD   
17     -77.049435    38.916502              1              CALIFORNIA ST   
18     -77.049782    38.916382              1                   TRACY PL   
19     -76.941487    38.882218              1                 CHAPLIN ST   
20     -77.072576    38.969719              1             RITTENHOUSE ST   
21     -77.072321    38.918272              1                  TUNLAW RD   
22     -77.074048    38.921291              1                  TUNLAW RD   
23     -77.075185    38.922502              1                 CALVERT ST   
24     -77.074198    38.928979              1              CATHEDRAL AVE   
25     -77.093361    38.941329              1                  TILDEN ST   
26     -76.999745    38.836787              1            MISSISSIPPI AVE   
27     -77.090684    38.950087              1                    46TH ST   
28     -77.086737    38.952166              1               DAVENPORT ST   
29     -77.088183    38.948859              1             BUTTERWORTH PL   
30     -77.078994    38.956519              1                HARRISON ST   
31     -77.080901    38.908419              1                    44TH ST   
32     -76.975226    38.856613              1                   BRUCE PL   
33     -76.957663    38.890442              1             KENILWORTH AVE   
34     -76.951787    38.889789              2            EAST CAPITOL ST   
35     -76.952260    38.895798              1                 BENNING RD   
36     -76.960825    38.889793              2            EAST CAPITOL ST   
37     -77.092827    38.942169              1                   UPTON ST   
38     -77.099312    38.927759              1               ESKRIDGE TER   
39     -77.082094    38.954766              1                    42ND ST   
40     -77.083708    38.958331              1                    43RD ST   
41     -77.083280    38.959867              1                    42ND PL   
42     -77.086271    38.955025              1                    44TH ST   
43     -77.085211    38.945169              1                  WINDOM PL   
44     -77.094418    38.919246              1                       W ST   
45     -77.092787    38.925338              1                 DEXTER TER   
46     -77.085873    38.949653              1              BRANDYWINE ST   
47     -77.082767    38.949648              1              BRANDYWINE ST   
48     -77.076988    38.927788              1                    39TH ST   
49     -77.072070    38.925076              1                    36TH PL   
50     -77.072550    38.924548              1                    36TH PL   
51     -76.939339    38.887969              1        

In [47]:
df_lights['number_lights'].value_counts()

1      67519
2       2903
5         97
4         65
3         55
6         51
8         18
7         10
10         7
9          5
12         3
54         2
13         2
11         1
116        1
14         1
15         1
18         1
29         1
222        1
34         1
232        1
42         1
192        1
Name: number_lights, dtype: int64

In [48]:
light_count = df_lights.groupby('streetsegid')['number_lights'].count()

In [49]:
light_count.head()

streetsegid
SEGID-1        11
SEGID-10        4
SEGID-1000      5
SEGID-10000     5
SEGID-10001     4
Name: number_lights, dtype: int64

In [50]:
light_count.reset_index(drop=False)
light_count = pd.DataFrame(light_count)

In [51]:
light_count.head()

number_lights
streetsegid               
SEGID-1                 11
SEGID-10                 4
SEGID-1000               5
SEGID-10000              5
SEGID-10001              4

In [52]:
df_lights.drop(axis=1, columns=['number_lights'], inplace=True)

In [53]:
result = pd.concat(axis=1, objs=[df_lights, light_count])
result.head()

longitude_li  latitude_li streetname streetsegid  ward  number_lights
0    -77.035705    38.901943       K ST   SEGID-555   2.0            NaN
1    -76.985184    38.869033    14TH ST  SEGID-1661   8.0            NaN
2    -76.979626    38.863385       V ST  SEGID-2883   8.0            NaN
3    -76.971740    38.872472   WHITE PL  SEGID-2561   8.0            NaN
4    -76.974904    38.868505    22ND ST  SEGID-2645   8.0            NaN

In [54]:
df_lights.head()

longitude_li  latitude_li streetname streetsegid  ward
0    -77.035705    38.901943       K ST   SEGID-555     2
1    -76.985184    38.869033    14TH ST  SEGID-1661     8
2    -76.979626    38.863385       V ST  SEGID-2883     8
3    -76.971740    38.872472   WHITE PL  SEGID-2561     8
4    -76.974904    38.868505    22ND ST  SEGID-2645     8

In [55]:
# Total number of lights per segid
light_count['number_lights'].value_counts()

3     1798
4     1753
5     1465
2     1443
6     1081
1      913
7      800
8      605
9      469
10     373
11     284
12     227
13     180
14     122
15      97
16      81
17      64
18      63
19      36
20      33
21      32
23      22
22      22
24      13
26      12
27       9
29       8
25       7
28       6
32       5
30       4
34       3
63       3
31       3
47       3
42       2
38       2
88       2
53       2
40       2
41       2
39       2
36       2
55       2
35       2
43       2
69       1
48       1
64       1
80       1
46       1
67       1
57       1
61       1
49       1
59       1
81       1
97       1
45       1
37       1
76       1
68       1
60       1
44       1
91       1
Name: number_lights, dtype: int64

In [56]:
light_count.head()

number_lights
streetsegid               
SEGID-1                 11
SEGID-10                 4
SEGID-1000               5
SEGID-10000              5
SEGID-10001              4

In [57]:
len(light_count['number_lights'])

12080

In [58]:
df_final = pd.merge(df_final, light_count, how='left', on='streetsegid')

In [59]:
df_final.head(200)

streetsegid                            street_address  directionality  \
0       SEGID-1                              BANGOR ST SE             2.0   
1       SEGID-2                           SOUTHERN AVE SE             2.0   
2       SEGID-3                           100 F STREET NE             0.0   
3       SEGID-3                           100 F STREET NE             0.0   
4       SEGID-4                                   O ST NW             2.0   
5       SEGID-5                  FLORIDA AVE NE / P ST NE             2.0   
6       SEGID-6                               GALEN ST SE             2.0   
7       SEGID-7                                18TH ST SE             2.0   
8       SEGID-8                                12TH ST NW             0.0   
9       SEGID-9                                14TH ST NE             2.0   
10     SEGID-10                                 4TH ST SE             0.0   
11     SEGID-11                                   O ST NW             2.0   
12     SEGID-12                                   T ST NW             1.0   
13     SEGID-13                            WHITTIER ST NW             2.0   
14     SEGID-14                            INDIANA AVE NW             2.0   
15     SEGID-14                            INDIANA AVE NW             2.0   
16     SEGID-14                            INDIANA AVE NW             2.0   
17     SEGID-14                            INDIANA AVE NW             2.0   
18     SEGID-15                                19TH ST NW             1.0   
19     SEGID-15                                19TH ST NW             1.0   
20     SEGID-16                           MARYLAND AVE SW             2.0   
21     SEGID-17                                 8TH ST NW             2.0   
22     SEGID-18                             WEBSTER ST NW             0.0   
23     SEGID-19                                   K ST SE             1.0   
24     SEGID-20                           HOLBROOK TER NE             2.0   
25     SEGID-22                         KENILWORTH AVE NE             0.0   
26     SEGID-23                                13TH ST SE             2.0   
27     SEGID-24                          CHESAPEAKE ST NW             2.0   
28     SEGID-25                                30TH ST SE             2.0   
29     SEGID-26                                   H ST NE             2.0   
30     SEGID-27                                   C ST NE             1.0   
31     SEGID-28               239 MASSACHUSETTS AVENUE NE             0.0   
32     SEGID-29                                 4TH ST NE             1.0   
33     SEGID-30                                   P ST NW             2.0   
34     SEGID-32                                10TH ST NW             1.0   
35     SEGID-33                              CORBIN PL NE             1.0   
36     SEGID-34                   1500 TRINIDAD AVENUE NE             0.0   
37     SEGID-35                           MONTELLO AVE NE             1.0   
38     SEGID-36                                   Q ST SE             2.0   
39     SEGID-37                                   K ST SE             0.0   
40     SEGID-38                               ALLEN PL NW             2.0   
41     SEGID-39                                   B ST SE             0.0   
42     SEGID-40                                52ND ST NE             2.0   
43     SEGID-41                       SOUTH DAKOTA AVE NE             2.0   
44     SEGID-42                            CENTRAL AVE NE             2.0   
45     SEGID-43                       SOUTH DAKOTA AVE NE             2.0   
46     SEGID-44                                   H ST NW             1.0   
47     SEGID-45                             HILLYER PL NW             1.0   
48     SEGID-46                                   O ST NE             2.0   
49     SEGID-47                         BLADENSBURG RD NE             2.0   
50     SEGID-48                                17TH ST NW             1.0   


In [60]:
df_bikelane = pd.read_csv('Processed Data/Bike_Lane.csv')

In [61]:
df_bikelane = df_bikelane.loc[:, ['streetsegid','sourceid', 'bikelanelength','facility', 'shape_length']]

In [62]:
len(df_bikelane)

1370

In [63]:
df_bikelane.columns

Index(['streetsegid', 'sourceid', 'bikelanelength', 'facility',
       'shape_length'],
      dtype='object')

In [64]:
df_bikelane[df_bikelane['streetsegid'] == 0 ]

streetsegid  sourceid  bikelanelength            facility  shape_length
625            0                  0.089889  Existing Bike Lane    144.661996
690            0                  0.000000                       2151.818619
708            0  12463180        0.036911  Existing Bike Lane     59.402888

In [65]:
df_bikelane.drop([625, 690, 708], inplace=True)

In [66]:
df_bikelane['streetsegid'].isna().value_counts()

False    1367
Name: streetsegid, dtype: int64

In [67]:
df_bikelane['streetsegid'] = df_bikelane['streetsegid'].astype(str)
df_bikelane['streetsegid'] = 'SEGID-' + df_bikelane['streetsegid']

In [68]:
df_bikelane.head()

streetsegid  sourceid  bikelanelength            facility  shape_length
0   SEGID-9854  15135550        0.009455  Existing Bike Lane     15.216846
1  SEGID-10198  15135555        0.076754  Existing Bike Lane    123.524976
2   SEGID-9167  15135560        0.058610  Existing Bike Lane     94.322895
3  SEGID-12337  15135565        0.026891  Existing Bike Lane     43.276471
4  SEGID-10611  15135580        0.172385  Existing Bike Lane    277.425702

In [69]:
df_final = pd.merge(df_final, df_bikelane, how='left', on='streetsegid')

In [70]:
df_final.head(2000)

streetsegid                                street_address  \
0        SEGID-1                                  BANGOR ST SE   
1        SEGID-2                               SOUTHERN AVE SE   
2        SEGID-3                               100 F STREET NE   
3        SEGID-3                               100 F STREET NE   
4        SEGID-4                                       O ST NW   
5        SEGID-5                      FLORIDA AVE NE / P ST NE   
6        SEGID-6                                   GALEN ST SE   
7        SEGID-7                                    18TH ST SE   
8        SEGID-8                                    12TH ST NW   
9        SEGID-9                                    14TH ST NE   
10      SEGID-10                                     4TH ST SE   
11      SEGID-11                                       O ST NW   
12      SEGID-12                                       T ST NW   
13      SEGID-13                                WHITTIER ST NW   
14      SEGID-14                                INDIANA AVE NW   
15      SEGID-14                                INDIANA AVE NW   
16      SEGID-14                                INDIANA AVE NW   
17      SEGID-14                                INDIANA AVE NW   
18      SEGID-15                                    19TH ST NW   
19      SEGID-15                                    19TH ST NW   
20      SEGID-16                               MARYLAND AVE SW   
21      SEGID-17                                     8TH ST NW   
22      SEGID-18                                 WEBSTER ST NW   
23      SEGID-19                                       K ST SE   
24      SEGID-20                               HOLBROOK TER NE   
25      SEGID-22                             KENILWORTH AVE NE   
26      SEGID-23                                    13TH ST SE   
27      SEGID-24                              CHESAPEAKE ST NW   
28      SEGID-25                                    30TH ST SE   
29      SEGID-26                                       H ST NE   
30      SEGID-27                                       C ST NE   
31      SEGID-28                   239 MASSACHUSETTS AVENUE NE   
32      SEGID-29                                     4TH ST NE   
33      SEGID-30                                       P ST NW   
34      SEGID-32                                    10TH ST NW   
35      SEGID-33                                  CORBIN PL NE   
36      SEGID-34                       1500 TRINIDAD AVENUE NE   
37      SEGID-35                               MONTELLO AVE NE   
38      SEGID-36                                       Q ST SE   
39      SEGID-37                                       K ST SE   
40      SEGID-38                                   ALLEN PL NW   
41      SEGID-39                                       B ST SE   
42      SEGID-40                                    52ND ST NE   
43      SEGID-41                           SOUTH DAKOTA AVE NE   
44      SEGID-42                                CENTRAL AVE NE   
45      SEGID-43                           SOUTH DAKOTA AVE NE   
46      SEGID-44                                       H ST NW   
47      SEGID-45                                 HILLYER PL NW   
48      SEGID-46                                       O ST NE   
49      SEGID-47                             BLADENSBURG RD NE   
50      SEGID-48                                    17TH ST NW   
51      SEGID-49                              WILTBERGER ST NW   
52      SEGID-50                          MASSACHUSETTS AVE NW   
53      SEGID-51                               LEXINGTON PL NE   
54      SEGID-52                      14TH ST NW & CLIFTON ST    
55      SEGID-53              FLORIDA AVENUE NW & 10TH STREET    
56      SEGID-54                                    HIGH ST SE   
57      SEGID-55                                    21ST ST NW   
58      SEGID-56                    18TH STREET NW & L STREET    
59      SEGID-56                             

In [71]:
df_final.to_csv('Processed Data/final_frame.csv', index=False)

In [72]:
df_final = pd.read_csv('Processed Data/final_frame.csv')

C:\Users\602770\AppData\Local\Continuum\anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3049: DtypeWarning: Columns (15,16,17,18) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [73]:
df_final.head(200)

streetsegid                            street_address  directionality  \
0       SEGID-1                              BANGOR ST SE             2.0   
1       SEGID-2                           SOUTHERN AVE SE             2.0   
2       SEGID-3                           100 F STREET NE             0.0   
3       SEGID-3                           100 F STREET NE             0.0   
4       SEGID-4                                   O ST NW             2.0   
5       SEGID-5                  FLORIDA AVE NE / P ST NE             2.0   
6       SEGID-6                               GALEN ST SE             2.0   
7       SEGID-7                                18TH ST SE             2.0   
8       SEGID-8                                12TH ST NW             0.0   
9       SEGID-9                                14TH ST NE             2.0   
10     SEGID-10                                 4TH ST SE             0.0   
11     SEGID-11                                   O ST NW             2.0   
12     SEGID-12                                   T ST NW             1.0   
13     SEGID-13                            WHITTIER ST NW             2.0   
14     SEGID-14                            INDIANA AVE NW             2.0   
15     SEGID-14                            INDIANA AVE NW             2.0   
16     SEGID-14                            INDIANA AVE NW             2.0   
17     SEGID-14                            INDIANA AVE NW             2.0   
18     SEGID-15                                19TH ST NW             1.0   
19     SEGID-15                                19TH ST NW             1.0   
20     SEGID-16                           MARYLAND AVE SW             2.0   
21     SEGID-17                                 8TH ST NW             2.0   
22     SEGID-18                             WEBSTER ST NW             0.0   
23     SEGID-19                                   K ST SE             1.0   
24     SEGID-20                           HOLBROOK TER NE             2.0   
25     SEGID-22                         KENILWORTH AVE NE             0.0   
26     SEGID-23                                13TH ST SE             2.0   
27     SEGID-24                          CHESAPEAKE ST NW             2.0   
28     SEGID-25                                30TH ST SE             2.0   
29     SEGID-26                                   H ST NE             2.0   
30     SEGID-27                                   C ST NE             1.0   
31     SEGID-28               239 MASSACHUSETTS AVENUE NE             0.0   
32     SEGID-29                                 4TH ST NE             1.0   
33     SEGID-30                                   P ST NW             2.0   
34     SEGID-32                                10TH ST NW             1.0   
35     SEGID-33                              CORBIN PL NE             1.0   
36     SEGID-34                   1500 TRINIDAD AVENUE NE             0.0   
37     SEGID-35                           MONTELLO AVE NE             1.0   
38     SEGID-36                                   Q ST SE             2.0   
39     SEGID-37                                   K ST SE             0.0   
40     SEGID-38                               ALLEN PL NW             2.0   
41     SEGID-39                                   B ST SE             0.0   
42     SEGID-40                                52ND ST NE             2.0   
43     SEGID-41                       SOUTH DAKOTA AVE NE             2.0   
44     SEGID-42                            CENTRAL AVE NE             2.0   
45     SEGID-43                       SOUTH DAKOTA AVE NE             2.0   
46     SEGID-44                                   H ST NW             1.0   
47     SEGID-45                             HILLYER PL NW             1.0   
48     SEGID-46                                   O ST NE             2.0   
49     SEGID-47                         BLADENSBURG RD NE             2.0   
50     SEGID-48                                17TH ST NW             1.0   
